# **Consultant of Network Attack Detection**

deskripsi (ada di pdf).
Network Intrusion Detection  System (NIDS)

## **Goal**

Dari data network traffic -> detect attack

## **Source of the dataset**

GDrive: [click here](https://drive.google.com/drive/folders/1lOz8fx9AI7lWSEN9myIn18RmMrPErq8D?usp=drive_link)

## **Atribute Information**

The inputs (Var X/independent var) are as follows

- duration
- protocol_type
- service
- flag
- src_bytes
- dst_bytes
- land
- wrong_fragment
- urgent
- hot
- num_failed_logins
- logged_in
- num_compromised
- root_shell
- su_attempted
- num_root
- num_file_creations
- num_shells
- num_access_files
- num_outbound_cmds
- is_host_login
- is_guest_login
- count
- srv_count
- serror_rate
- srv_serror_rate
- rerror_rate
- srv_rerror_rate
- same_srv_rate
- diff_srv_rate
- srv_diff_host_rate
- dst_host_count
- dst_host_srv_count
- dst_host_same_srv_rate
- dst_host_diff_srv_rate
- dst_host_same_src_port_rate
- dst_host_srv_diff_host_rate
- dst_host_serror_rate
- dst_host_srv_serror_rate
- dst_host_rerror_rate
- dst_host_srv_rerror_rate
- type_of_attack

The output (target/Y/dependent var) is as follow:

- detect attack

# **Import Library**

In [11]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns

from ydata_profiling import ProfileReport

# **1. Import Dataset**

In [15]:
# Path to training and validation dataset
train_PATH = 'D:\DAC-2023\Dataset\DataTrain_Preliminary.csv'
pred_PATH = 'D:\DAC-2023\Dataset\Data_Prediction.csv'

As a network attack detection consultant, we have been provided with two datasets: one for training and one for prediction. With these datasets, we can already narrow down the scope of our analysis, which in this case is creating a predictive model. Predictive model will naturally involve machine learning techniques. However, the field of machine learning itself is quite broad.

Therefore, we will begin by closely examining the data to refine our analysis to choose the best algorithm to discover the predictive model for effective network attack detection. This process involves exploring the data, identifying relevant features, and iteratively refining our approach until we find the most suitable predictive model.

In [16]:
# Load training data 
df_train = pd.read_csv(train_PATH, delimiter=';')
df_train.head()

duration protocol_type  service flag src_bytes dst_bytes land  \
0        0           tcp  private   SH         0         0    0   
1        0           tcp  private   S0         0         0    0   
2        0           tcp     http   SF       285      3623    0   
3        0           tcp     http   SF       232       584    0   
4        1           tcp     smtp   SF      1080       327    0   

  wrong_fragment urgent hot  ... dst_host_srv_count dst_host_same_srv_rate  \
0              0      0   0  ...                  1                   0.01   
1              0      0   0  ...                  5                   0.02   
2              0      0   0  ...                228                   1.00   
3              0      0   0  ...                255                   1.00   
4              0      0   0  ...                154                   0.58   

  dst_host_diff_srv_rate dst_host_same_src_port_rate  \
0                   0.94                        0.95   
1                   0.08                        0.00   
2                   0.00                        0.01   
3                   0.00                        0.17   
4                   0.02                        0.00   

  dst_host_srv_diff_host_rate dst_host_serror_rate dst_host_srv_serror_rate  \
0                           0                 0.95                        1   
1                           0                 1.00                        1   
2                           *                 0.00                        0   
3                           *                 0.00                        0   
4                           *                 0.00                        0   

  dst_host_rerror_rate dst_host_srv_rerror_rate type_of_attack  
0                    0                        0           nmap  
1                    0                        0        neptune  
2                    0                        0         normal  
3                    0                        0         normal  
4                    0                        0         normal  

[5 rows x 42 columns]

In [17]:
# The shape of training data
df_train.shape

(112446, 42)

In [18]:
# Load validiation data 
df_pred = pd.read_csv(pred_PATH, delimiter=';')
df_pred.head()

id  duration protocol_type   service flag  src_bytes  dst_bytes  land  \
0   1         1           tcp      smtp   SF       2397        328     0   
1   2       990           udp     other   SF        145        105     0   
2   3         0          icmp     ecr_i   SF       1032          0     0   
3   4         0          icmp     eco_i   SF          8          0     0   
4   5         0           udp  domain_u   SF         44        132     0   

   wrong_fragment  urgent  ...  dst_host_count  dst_host_srv_count  \
0               0       0  ...             179                 182   
1               0       0  ...             255                   1   
2               0       0  ...             255                  23   
3               0       0  ...               1                  85   
4               0       0  ...             250                 101   

   dst_host_same_srv_rate  dst_host_diff_srv_rate  \
0                    0.68                    0.02   
1                    0.00                    0.64   
2                    0.09                    0.02   
3                    1.00                    0.00   
4                    0.40                    0.01   

   dst_host_same_src_port_rate  dst_host_srv_diff_host_rate  \
0                         0.01                         0.01   
1                         0.94                         0.00   
2                         0.09                         0.00   
3                         1.00                         0.51   
4                         0.38                         0.00   

   dst_host_serror_rate  dst_host_srv_serror_rate  dst_host_rerror_rate  \
0                   0.0                       0.0                   0.0   
1                   0.0                       0.0                   0.0   
2                   0.0                       0.0                   0.0   
3                   0.0                       0.0                   0.0   
4                   0.0                       0.0                   0.0   

   dst_host_srv_rerror_rate  
0                       0.0  
1                       0.0  
2                       0.0  
3                       0.0  
4                       0.0  

[5 rows x 42 columns]

In [19]:
# The shape of validation data
df_pred.shape

(12479, 42)

## **Handling NaN Value**

In [39]:
nan_sum = df_train.isnull().sum()
nan_sum = nan_sum[nan_sum > 0]
nan_sum

protocol_type                   668
service                        1020
flag                            853
dst_host_same_srv_rate          328
dst_host_diff_srv_rate          243
dst_host_same_src_port_rate     438
dst_host_serror_rate            428
dtype: int64

In [40]:
# how many total missing values do we have?
total_cells = np.product(df_train.shape)
total_missing = nan_sum.sum()

# percent of data that is missing
percent_missing = (total_missing/total_cells)*100
print(f"{percent_missing:.1f}%")

0.1%


Because the nan value is only 0.1% of the data 

In [41]:
df_train_cleaned = df_train.dropna()

In [44]:
df_train_cleaned.shape

(108666, 42)

## **Handling Duplicate Data**

## **Feature Description**

In [10]:
# Column difference between training and validation dataset
train_cols = set(df_train.columns)
pred_cols = set(df_pred.columns)

print("Columns in df_train but not in df_pred:", train_cols - pred_cols)
print("Columns in df_pred but not in df_train:", pred_cols - train_cols)

Columns in df_train but not in df_pred: {'type_of_attack'}
Columns in df_pred but not in df_train: {'id'}


In the provided training dataset, we have a crucial column called "type_of_attack." This column serves as our target or label variable, which means it contains the information we want our predictive model to learn and predict. To determine the appropriate predictive model, we will thoroughly analyze the "type_of_attack" column. Here's a clear breakdown of the steps involved:

### **Understanding the Label (type_of_attack)**

 The "type_of_attack" column likely contains different categories or labels that represent various types of network attacks. To select an appropriate predictive model, we need to gain a deep understanding of these attack types. 

In [20]:
# Identifying and listing the unique attack types present in the column
attack_type = df_train['type_of_attack'].unique()
print(f"Value contain in type_of_attack column:\n{attack_type}")

Value contain in type_of_attack column:
['nmap' 'neptune' 'normal' 'Denial of Service Attack' 'portsweep' 'satan'
 'ipsweep' 'smurf']


There are 8 type of network attack in this training data. Based on (reference), 

Normal -> not an attack

DOS ATTACK: 
neptune -> working to SYN flood Denial of Service on one or more ports, Neptune attack make the memory resources busy by sending TCP packet requesting to initiate a TCP session,
DOS ->  makes the computer system to be hectic by sending many ping, 
Smurf -> Denial of Service ICMP echo reply flood. 

PROBE: nmap, portsweep, satan, ipsweep, 

In [28]:
# Exploring the distribution of these attack types to understand their prevalence in the dataset.
attack_type_counts = df_train['type_of_attack'].value_counts()
attack_type_counts

type_of_attack
normal                      60538
neptune                     37142
ipsweep                      3254
satan                        3248
portsweep                    2687
smurf                        2394
Denial of Service Attack     1861
nmap                         1322
Name: count, dtype: int64

In [30]:
total_samples = len(df_train)
attack_type_percentages = (attack_type_counts / total_samples) * 100

TYPE OF ATTACK :
- nmap
- neptune
- normal
- Denial of Service Attack
- portsweep
- satan
- ipsweep
- smurf

This paper focused on Neptune and Smurf types of attack. Those attack characterized as DoS Attack. Dos Attack makes the computer system to be hectic by sending many ping. Neptune attack working to SYN flood Denial of Service on one or more ports while the function of Smurf attack is Denial of Service ICMP echo reply flood. Neptune attack make the memory resources busy by sending TCP packet requesting to initiate a TCP session.  After many TCP packet sent, the computer system finally runs out of memory resources. Smurf attack is the popular type of attack sending ICMP echo request packet to middle device. ICMP packets have source address name as victim’s IP address and middle device address as destination address. DoS attack reduces the performance of server by overflowing the ICMP traffic as discussed above in the Neptune and Smurf attack. So, detection of DoS attack is very significant to protect the system. 

KOLOM KUNCI:
- protocol type
- port
- 

In [49]:
def filtered_by_type_of_attack(df, values):
    filtered = df[df['type_of_attack'] == values]
    return filtered

In [54]:
def sum_of_nan_value(df):
    nan_sum = df.isnull().sum()
    nan_sum = nan_sum [nan_sum  > 0]
    return nan_sum 

#### **Normal**

In [58]:
normal = filtered_by_type_of_attack(df_train, 'normal')
sum_of_nan_value(normal)

protocol_type                  494
service                        359
flag                           514
dst_host_same_srv_rate         183
dst_host_diff_srv_rate         198
dst_host_same_src_port_rate    438
dst_host_serror_rate           240
dtype: int64

#### **DoS Attack**
dos, neptune, smurf

In [60]:
dos = filtered_by_type_of_attack(df_train, 'Denial of Service Attack')
sum_of_nan_value(dos)

protocol_type    24
service          36
flag             26
dtype: int64

In [56]:
neptune = filtered_by_type_of_attack(df_train, 'neptune')
sum_of_nan_value(neptune)

protocol_type              93
service                   132
flag                      121
dst_host_same_srv_rate     27
dst_host_serror_rate      169
dtype: int64

In [59]:
smurf = filtered_by_type_of_attack(df_train, 'smurf')
sum_of_nan_value(smurf)

protocol_type              57
dst_host_same_srv_rate    118
dtype: int64

In [70]:
x = smurf[['protocol_type', 'type_of_attack']]
x

protocol_type type_of_attack
61              icmp          smurf
81              icmp          smurf
375             icmp          smurf
419             icmp          smurf
483             icmp          smurf
...              ...            ...
112229          icmp          smurf
112309          icmp          smurf
112310          icmp          smurf
112350          icmp          smurf
112352          icmp          smurf

[2394 rows x 2 columns]

In [72]:
x.protocol_type.unique()

array(['icmp', nan], dtype=object)

In [74]:
smurf.service.unique()

array(['ecr_i'], dtype=object)

In [75]:
smurf.flag.unique()

array(['SF'], dtype=object)

#### **Probe**
nmap, portsweep, satan, ipsweep

In [57]:
nmap = filtered_by_type_of_attack(df_train, 'nmap')
sum_of_nan_value(nmap)

service    67
flag       43
dtype: int64

In [61]:
portsweep = filtered_by_type_of_attack(df_train, 'portsweep')
sum_of_nan_value(portsweep)

service    37
flag       89
dtype: int64

In [62]:
satan = filtered_by_type_of_attack(df_train, 'satan')
sum_of_nan_value(satan)

service    284
flag        31
dtype: int64

In [63]:
ipsweep = filtered_by_type_of_attack(df_train, 'ipsweep')
sum_of_nan_value(ipsweep)

service                   105
flag                       29
dst_host_diff_srv_rate     45
dst_host_serror_rate       19
dtype: int64

In [76]:
ProfileReport(df_train)

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

## **Duplicate Data**

In [20]:
duplicates = df_train[df_train.duplicated()]

In [21]:
duplicates

duration protocol_type  service flag src_bytes dst_bytes land  \
2439          0           tcp    other  REJ         0         0    0   
3041          0           tcp     http  REJ         0         0    0   
3411          0           tcp     http  REJ         0         0    0   
4164          0           tcp    other  REJ         0         0    0   
4714          0          icmp    eco_i   SF         8         0    0   
...         ...           ...      ...  ...       ...       ...  ...   
112304        0           tcp    other  REJ         0         0    0   
112320        0           tcp    other  REJ         0         0    0   
112383        0           tcp    other  REJ         0         0    0   
112389        0           tcp  private   S0         0         0    0   
112441        0           tcp     http  REJ         0         0    0   

       wrong_fragment urgent hot  ... dst_host_srv_count  \
2439                0      0   0  ...                  1   
3041                0      0   0  ...                255   
3411                0      0   0  ...                255   
4164                0      0   0  ...                  1   
4714                0      0   0  ...                 73   
...               ...    ...  ..  ...                ...   
112304              0      0   0  ...                  1   
112320              0      0   0  ...                  1   
112383              0      0   0  ...                  1   
112389              0      0   0  ...                 23   
112441              0      0   0  ...                255   

       dst_host_same_srv_rate dst_host_diff_srv_rate  \
2439                     0.00                   1.00   
3041                     1.00                   0.00   
3411                     1.00                   0.00   
4164                     0.00                   1.00   
4714                     1.00                   0.00   
...                       ...                    ...   
112304                   0.00                   1.00   
112320                   0.00                   1.00   
112383                   0.00                   1.00   
112389                   0.09                   0.06   
112441                   1.00                   0.00   

       dst_host_same_src_port_rate dst_host_srv_diff_host_rate  \
2439                          0.00                           0   
3041                          0.50                           *   
3411                          0.50                           *   
4164                          0.00                           0   
4714                          1.00                           *   
...                            ...                         ...   
112304                        0.00                           0   
112320                        0.00                           0   
112383                        0.00                           0   
112389                        0.00                           0   
112441                        0.14                           *   

       dst_host_serror_rate dst_host_srv_serror_rate dst_host_rerror_rate  \
2439                   0.26                        0                    *   
3041                   0.00                        0                    1   
3411                   0.00                        0                    1   
4164                   0.18                        0                    *   
4714                   0.00                        0                    0   
...                     ...                      ...                  ...   
112304                 0.19                        0                    *   
112320                 0.24                        0                    *   
112383                 0.10                        0                    *   
112389                 1.00                        1                    0   
112441                 0.00                        0                    *   

       dst_host_srv_rerror_rat

is it really duplicate? harus nemu variabel kunci yg menentukan itu row duplicate or no. atau jangan jangan nilai duplicate ini bisa jadi kunci network attack (karena patternnya sama)